In [1]:
%pip install scikit-lego

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 216.7/216.7 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 188.9/188.9 kB 5.0 MB/s eta 0:00:00


In [21]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from sklearn.linear_model import LinearRegression
from sklego.linear_model import LADRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

In [9]:
df = pd.read_csv("hf://datasets/maharshipandya/spotify-tracks-dataset/dataset.csv")

In [4]:
# Data Cleaning Function
def clean_data(df):
  df = df.drop('Unnamed: 0', axis=1, errors='ignore')
  df = df.dropna()
  return df

# Apply the function to the DataFrame
spotify_clean = clean_data(df)

In [7]:
# Split data into train and test
from sklearn.model_selection import train_test_split
train_spotify, val_spotify = train_test_split(spotify_clean, test_size=0.2, random_state=42)

# **Stage 4: Linear Regression**

2. Choosing 'danceability' to predict 'popularity'

## Simple Linear Regression

3. Modeling regression and calculating evaluation metrics on training and validation sets.

In [25]:
# LAD and LS on train
# LAD
lad_pop_fit = LADRegression()
lad_pop_fit.fit(X=np.array(train_spotify['danceability']).reshape(-1, 1), y=train_spotify['popularity'])


LADRegression()

In [26]:
# LS
ls_pop_fit = LinearRegression()
ls_pop_fit.fit(X=np.array(train_spotify['danceability']).reshape(-1, 1), y=train_spotify['popularity'])

LinearRegression()

In [29]:
# Plot
# Add to scatter plot of popularity vs. danceability
fig = px.scatter(train_spotify, x='danceability', y='popularity', title='Popularity vs. Danceability')
fig.add_trace(
    go.Scatter(
        x=train_spotify['danceability'],
        y=lad_pop_fit.intercept_ + train_spotify['danceability'] * lad_pop_fit.coef_[0],
        mode='lines',
        name='LAD',
        line={'dash': 'dash',
              'color': 'black'})
)

fig.add_trace(
    go.Scatter(
        x=train_spotify['danceability'],
        y=ls_pop_fit.intercept_ + train_spotify['danceability'] * ls_pop_fit.coef_[0],
        mode='lines',
        name='LS',
        line={'dash': 'solid',
              'color': 'black'})
)

In [34]:
# Evaluate based on error metrics
pred_train_df = pd.DataFrame(
    {'true': train_spotify['popularity'],
     'ls_pred': ls_pop_fit.predict(np.array(train_spotify['danceability']).reshape(-1, 1)),
     'lad_pred': lad_pop_fit.predict(np.array(train_spotify['danceability']).reshape(-1, 1))})
pred_train_df.head()

true    ls_pred   lad_pred
96253    41  33.631190  35.602122
70417    52  33.752381  35.960212
66688    11  34.282032  37.525199
51391    61  33.936413  36.503979
95123    37  34.282032  37.525199

In [31]:
# calculate the rMSE, MAE, MAD, correlation, and R2 of the popularity with the LS and LAD predictions
print('LS rMSE:', np.sqrt(mean_squared_error(pred_train_df['true'], pred_train_df['ls_pred'])))
print('LS MAE:', mean_absolute_error(pred_train_df['true'], pred_train_df['ls_pred']))
print('LS MAD:', np.median(np.abs(pred_train_df['true'] - pred_train_df['ls_pred'])))
print('LS correlation:', np.corrcoef(pred_train_df['true'], pred_train_df['ls_pred'])[0, 1])
print('LS R2:', r2_score(pred_train_df['true'], pred_train_df['ls_pred']))

print('LAD rMSE:', np.sqrt(mean_squared_error(pred_train_df['true'], pred_train_df['lad_pred'])))
print('LAD MAE:', mean_absolute_error(pred_train_df['true'], pred_train_df['lad_pred']))
print('LAD MAD:', np.median(np.abs(pred_train_df['true'] - pred_train_df['lad_pred'])))
print('LAD correlation:', np.corrcoef(pred_train_df['true'], pred_train_df['lad_pred'])[0, 1])
print('LAD R2:', r2_score(pred_train_df['true'], pred_train_df['lad_pred']))

LS rMSE: 22.298835590275154
LS MAE: 18.849795903530605
LS MAD: 16.5089058197971
LS correlation: 0.03486667502135334
LS R2: 0.0012156850270447217
LAD rMSE: 22.389626832601394
LAD MAE: 18.802315035389277
LAD MAD: 16.41644562338179
LAD correlation: 0.0348666750213534
LAD R2: -0.006934110517266223


In [35]:
# LAD and LS on test
pred_val_df = pd.DataFrame(
    {'true': val_spotify['popularity'],
     'ls_pred': ls_pop_fit.predict(np.array(val_spotify['danceability']).reshape(-1, 1)),
     'lad_pred': lad_pop_fit.predict(np.array(val_spotify['danceability']).reshape(-1, 1))})
pred_val_df.head()

true    ls_pred   lad_pred
113186    50  32.410300  31.994695
42819     11  31.521564  29.368700
59311      0  31.530541  29.395225
90417     34  32.634728  32.657825
61000     57  33.245173  34.461538

In [36]:
# Evaluate based on error metrics
# compute the rMSE, MAE, MAD, correlation and R2 of the popularity with the LS and LAD predictions
print('LS rMSE:', np.sqrt(mean_squared_error(pred_val_df['true'], pred_val_df['ls_pred'])))
print('LS MAE:', mean_absolute_error(pred_val_df['true'], pred_val_df['ls_pred']))
print('LS MAD:', np.median(np.abs(pred_val_df['true'] - pred_val_df['ls_pred'])))
print('LS correlation:', np.corrcoef(pred_val_df['true'], pred_val_df['ls_pred'])[0, 1])
print('LS R2:', r2_score(pred_val_df['true'], pred_val_df['ls_pred']))

print('LAD rMSE:', np.sqrt(mean_squared_error(pred_val_df['true'], pred_val_df['lad_pred'])))
print('LAD MAE:', mean_absolute_error(pred_val_df['true'], pred_val_df['lad_pred']))
print('LAD MAD:', np.median(np.abs(pred_val_df['true'] - pred_val_df['lad_pred'])))
print('LAD correlation:', np.corrcoef(pred_val_df['true'], pred_val_df['lad_pred'])[0, 1])
print('LAD R2:', r2_score(pred_val_df['true'], pred_val_df['lad_pred']))


LS rMSE: 22.259272885262504
LS MAE: 18.835055984452218
LS MAD: 16.579772539806168
LS correlation: 0.03770958846852154
LS R2: 0.0012381720316249067
LAD rMSE: 22.36415310454478
LAD MAE: 18.79332629484839
LAD MAD: 16.46949602119043
LAD correlation: 0.03770958846852156
LAD R2: -0.008195841292615524


4. Over/Underfitting?

Our model shows evidence of underffiting because the R squared value is so low for both LS and LAD. It is not able to predict well on the training dataset nor the validation set.

5. Regularization Technique: Ridge

In [38]:
train_spotify.head()

track_id                  artists  \
96253  2dBjh7rBHfTtKVIDY89g5G                Seu Jorge   
70417  3d09lKFNMjL28k0B0TcQhW                Chyi Chin   
66688  1IGSLXykccmp1TSqhYnden             Babyboomboom   
51391  67KTXqxMEyBMq3LApqCgNV  Sidhu Moose Wala;DIVINE   
95123  2Qx9yW1HKfX04jXSAbteiK                Rumbavana   

                                              album_name  \
96253  Musicas para Churrasco, Vol.1 (Ao Vivo) (Delux...   
70417                                            "1" (壹)   
66688                                 English and French   
51391                                          Moosetape   
95123                          Pa Que Lo Goces Con Ganas   

                                              track_name  popularity  \
96253                                 Carolina (Ao Vivo)          41   
70417                                              大約在冬季          52   
66688  Heads, Shoulders, Knees and Toes (Tête, Epaule...          11   
51391                         Moosedrilla (feat. DIVINE)          61   
95123                                       El Capitolio          37   

       duration_ms  explicit  danceability  energy  key  loudness  mode  \
96253       358733     False         0.641   0.880   11    -6.401     0   
70417       231520     False         0.668   0.361    5    -9.710     0   
66688        98386     False         0.786   0.225    9   -16.516     1   
51391       232173     False         0.709   0.829    0    -5.817     1   
95123       360320     False         0.786   0.702    0    -6.742     1   

       speechiness  acousticness  instrumentalness  liveness  valence  \
96253       0.0604        0.1510          0.000761     0.611    0.423   
70417       0.0353        0.7950          0.000000     0.246    0.432   
66688       0.5730        0.6790          0.000000     0.201    0.658   
51391       0.2450        0.0698          0.000000     0.561    0.654   
95123       0.0456        0.5110          0.000000     0.120    0.696   

         tempo  time_signature track_genre  
96253   93.000               4       samba  
70417   73.919               3    mandopop  
66688  110.066               4        kids  
51391  137.954               4     hip-hop  
95123  104.030               4       salsa

In [39]:
X = train_spotify.drop(columns=['popularity', 'track_name', 'artists', 'album_name', 'explicit', 'track_genre', 'track_id'])
# scale the predictors
X_std = (X - X.mean()) / X.std()
y = train_spotify['popularity']

In [40]:
from sklearn.linear_model import  Ridge, Lasso
from sklearn.model_selection import cross_val_score, cross_validate

# use 10-fold cross-validation to select the best lambda (alpha) value for the ridge regression model

# define the alpha values to test
# note that the start/stop values in the first two arguments are the exponents
alphas = np.logspace(-1, 6, 100)

# create an empty list to store the cross-validation scores
ridge_cv_scores = []

# create a for loop to compute the cross-validation score for each alpha value
for alpha in alphas:
    ridge = Ridge(alpha=alpha)
    ridge_cv = cross_validate(estimator=ridge,
                              X=X_std,
                              y=y,
                              cv=10,
                              scoring='neg_root_mean_squared_error')
    ridge_cv_scores.append({'alpha': alpha,
                            'log_alpha': np.log(alpha),
                            'test_mse': -np.mean(ridge_cv['test_score'])})

# convert the cross-validation scores into a data frame
ridge_cv_scores_df = pd.DataFrame(ridge_cv_scores)

# plot the cross-validation scores as a function of alpha
px.line(ridge_cv_scores_df,
        x='log_alpha',
        y='test_mse',
        title='Ridge')

In [42]:
ridge_cv_scores_df.head()

alpha  log_alpha   test_mse
0  0.100000  -2.302585  22.046221
1  0.117681  -2.139776  22.046221
2  0.138489  -1.976967  22.046221
3  0.162975  -1.814158  22.046221
4  0.191791  -1.651349  22.046221

In [43]:
# identify the value of alpha that minimizes the cross-validation score for ridge
ridge_alpha_min = ridge_cv_scores_df.sort_values(by='test_mse').head(1).alpha.values[0]
# compute the min MSE and the SE of the MSE
mse_se_ridge = ridge_cv_scores_df['test_mse'].std() / np.sqrt(10)
mse_min_ridge = ridge_cv_scores_df['test_mse'].min()


# identify the value of alpha that minimizes the cross-validation score for ridge within 1SE
ridge_alpha_1se = ridge_cv_scores_df[(ridge_cv_scores_df['test_mse'] <= mse_min_ridge + mse_se_ridge) &
                                     (ridge_cv_scores_df['test_mse'] >= mse_min_ridge - mse_se_ridge)].sort_values(by='alpha', ascending=False).head(1).alpha.values[0]



In [44]:
print('Ridge (min): ', ridge_alpha_min)
print('Ridge (1SE): ', ridge_alpha_1se)

Ridge (min):  403.70172585965537
Ridge (1SE):  20092.33002565046


In [45]:
# use ridge_alpha_min to fit the ridge regression model
ridge_min_fit = Ridge(alpha=ridge_alpha_min).fit(X=X_std, y=y)
ridge_1se_fit = Ridge(alpha=ridge_alpha_1se).fit(X=X_std, y=y)